In [1]:
import os # Operating System
import numpy as np
import pandas as pd
import datetime as dt # Datetime
import json # library to handle JSON files

!conda install -c conda-forge geopy --yes
import geocoder
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium #import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
# Set the present working directory
os.chdir("/resources/data/Coursera")

# Read the data for examination
df_ppd = pd.read_csv("Price_Paid_Data.csv")

# Assign meaningful column names
df_ppd.columns = ['TUID', 'Price', 'Date_Transfer', 'Postcode', 'Prop_Type', 'Old_New', 'Duration', 'PAON', \
                  'SAON', 'Street', 'Locality', 'Town_City', 'District', 'County', 'PPD_Cat_Type', 'Record_Status']

In [3]:
# Format the date column
df_ppd['Date_Transfer'] = df_ppd['Date_Transfer'].apply(pd.to_datetime)

# Sort by Date of Sale
df_ppd.sort_values(by=['Date_Transfer'],ascending=[False],inplace=True)

# Add a column with YEAR
df_ppd['Year'] = df_ppd['Date_Transfer'].dt.year

# Drop all transactions before 2016
df_ppd.drop(df_ppd[df_ppd.Date_Transfer.dt.year < 2016].index, inplace=True)

In [4]:
# Shape of my dataset
df_ppd.shape

(107711, 17)

In [6]:
# Let's find the shape again
df_ppd.shape

(105907, 17)

In [7]:
df_grp_year = df_ppd.groupby(['Year']).size()
df_grp_year

Year
2016       494
2017      2717
2018    102696
dtype: int64

In [8]:
df_ppd_london = df_ppd.query("Town_City == 'LONDON'")

In [9]:
districts = df_ppd_london['District'].unique().tolist()
len(districts)

29

In [10]:
town_city = df_ppd_london['Town_City'].unique().tolist()
len(town_city)

1

In [11]:
streets = df_ppd_london['Street'].unique().tolist()
len(streets)

4009

In [52]:
london_data = pd.read_csv("Street Coordinates London.csv")
london_data['Street'] = london_data['Street'].str.replace(', LONDON', '')

In [53]:
london_data.head(5)

Unnamed: 0               Street   Latitude  Longitude
0           0            GLYN ROAD  51.553247  -0.041384
1           1           MADGE HILL  51.515185  -0.342972
2           2         BROMLEY ROAD  51.430999  -0.015496
3           3  UPPER BROCKLEY ROAD  51.468664  -0.033001
4           4            SWAN ROAD  51.501136  -0.050552

In [82]:
df_grp_postcode.sort_values(ascending=[False],inplace=True)
df_grp_postcode.head(10)

Street               Town_City    County          
WESTFERRY CIRCUS     LONDON       GREATER LONDON      99750000.0
CHARTERHOUSE STREET  LONDON       GREATER LONDON      90000000.0
BLEEDING HEART YARD  LONDON       GREATER LONDON      90000000.0
PRIDE PARK           DERBY        CITY OF DERBY       81100000.0
BRIDGE ROAD          SOUTHALL     GREATER LONDON      76000000.0
STAFFORD AVENUE      HALIFAX      WEST YORKSHIRE      68776190.0
SAFFRON HILL         LONDON       GREATER LONDON      67635000.0
REDWONGS WAY         HUNTINGDON   CAMBRIDGESHIRE      66695709.0
PAVILION DRIVE       NORTHAMPTON  NORTHAMPTONSHIRE    60100000.0
BOLENESS ROAD        WISBECH      CAMBRIDGESHIRE      57708932.0
Name: Price, dtype: float64

In [14]:
address = 'London, UK'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of London City are 51.5073219, -0.1276474.


In [16]:
# create map of Manhattan using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=15)

# add markers to map
for lat, lng, label in zip(london_data['Latitude'], london_data['Longitude'], london_data['Street']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

In [33]:
df_grp_price = df_ppd_london.groupby(['Street'])['Price'].mean().reset_index()
df_grp_price.columns = ['Street', 'Avg_Price']

Street  Avg_Price
0     ABBESS CLOSE   265000.0
1   ABBEVILLE ROAD   790000.0
2    ABBEY GARDENS  4722750.0
3       ABBEY ROAD   944200.0
4  ABBEYFIELD ROAD   552500.0

In [46]:
df_affordable = df_grp_price.query("(Avg_Price >= 2000000) & (Avg_Price <= 2200000)")

In [ ]:
df_affordable

In [54]:
df_myhouse = pd.merge(london_data, df_affordable, on=['Street'], how='inner')

In [55]:
df_myhouse

Unnamed: 0              Street   Latitude  Longitude     Avg_Price
0          155       TREBOVIR ROAD  51.491394  -0.195395  2.000000e+06
1          242          IVOR PLACE  51.524330  -0.161365  2.155000e+06
2          380        BELTRAN ROAD  51.471158  -0.192537  2.025000e+06
3          668      QUEENS GARDENS  51.513457  -0.182547  2.067000e+06
4          825      CHEVENING ROAD  51.536921  -0.213468  2.028333e+06
5         1044         PORTEN ROAD  51.498603  -0.214120  2.200000e+06
6         1148     PLEYDELL AVENUE  51.496560  -0.246413  2.175000e+06
7         1237   CLARE LAWN AVENUE  51.458044  -0.265231  2.175000e+06
8         1550   BLENHEIM CRESCENT  51.515065  -0.208607  2.007500e+06
9         1629    HIGH ROAD LEYTON  51.562983  -0.010773  2.054935e+06
10        1718       PILGRIMS LANE  51.556195  -0.171283  2.085000e+06
11        2063      BROOMWOOD ROAD  51.454521  -0.159970  2.103550e+06
12        2070        MAIDA AVENUE  51.523443  -0.178738  2.145000e+06
13        2137     AIREDALE AVENUE  51.491212  -0.248038  2.115000e+06
14        2256      RANELAGH GROVE  51.490332  -0.151270  2.075000e+06
15        2360         WREN STREET  51.525334  -0.115505  2.050000e+06
16        2386     CHALCOT GARDENS  51.546488  -0.160949  2.200000e+06
17        2417         EDGE STREET  51.507703  -0.195097  2.200000e+06
18        2634   JOHN ISLIP STREET  51.491861  -0.128453  2.200000e+06
19        2644        HOLROYD ROAD  51.461464  -0.226527  2.100000e+06
20        2718  STREATHBOURNE ROAD  51.435702  -0.153329  2.125000e+06
21        2945       BUSHNELL ROAD  51.436504  -0.149785  2.200000e+06
22        3057    LILLIESHALL ROAD  51.465924  -0.144257  2.145000e+06
23        3123         CHEYNE WALK  51.482785  -0.170492  2.150000e+06
24        3137         CURZON ROAD  51.595583  -0.140844  2.125000e+06
25        3320              STRAND  51.511208  -0.119345  2.014212e+06
26        3330       HEREFORD MEWS  51.515495  -0.193545  2.162500e+06
27        3358        CHATHAM ROAD  51.455378  -0.162672  2.175000e+06
28        3509     RADSTOCK STREET  51.479066  -0.169416  2.200000e+06
29        3552          THE COMMON  51.529399  -0.061053  2.100000e+06
30        3901     WEDGWOOD VILLAS  51.550315  -0.184868  2.000000e+06
31        3919       BURGHLEY ROAD  51.555036  -0.141845  2.180000e+06

In [56]:
address = 'London, UK'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/lib/python3.6/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geograpical coordinate of London City are 51.5073219, -0.1276474.


In [66]:
# create map of Manhattan using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, price, street in zip(df_myhouse['Latitude'], df_myhouse['Longitude'], df_myhouse['Avg_Price'], df_myhouse['Street']):
    label = '{}, {}'.format(street, price)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

